# Multimode CLB
In the I/O section of the architecture, the `<mode>` tag was used to define different modes for the block. One mode was for input, the other mode for output. Modes are also used in CLBs. Open the file `OpenFPGA/tutorial/02_multimode_arch.xml`. It defines two modes for its CLB: either a 6-LUT, or two 5-LUTs with shared inputs.

Find the line `<pb_type name="clb" area="53894">` which begins the definition of the CLB. The next few lines define the inputs and outputs: 40 input pins, 20 output pins, and a clock pin. The inputs are marked with `equivalent="full"` which indicates that the inputs have logical equivalence so their locations may be freely swapped. The outputs are `equivalent="none"` so they may not be swapped.

The next primitive block is `<pb_type name="fle" num_pb="10">` which is a fracturable logic element that contains the two different modes of this CLB. There are 10 instances of this `fle` in the CLB. Each `fle` has 6 inputs, 2 outputs, and one clock pin.

### First Mode
`<mode name="n2_lut5">` begins the definition of the first mode. Moving down the architecture file, we see that in this mode, the `fle` contains one `lut5inter` block which contains two `ble5` blocks. The `ble5` blocks have 5 inputs and 1 output. The next group of lines define the LUT and FF in `ble5`.

Moving down to the second `<interconnect>` block:
```
<interconnect>
    <direct name="direct1" input="lut5inter.in" output="ble5[0:0].in"/>
    <direct name="direct2" input="lut5inter.in" output="ble5[1:1].in"/>
    <direct name="direct3" input="ble5[1:0].out" output="lut5inter.out"/>                 
    <complete name="complete1" input="lut5inter.clk" output="ble5[1:0].clk"/>                  
</interconnect>
```
we see that the input of `lut5inter` is connected to the inputs of both the first and second `ble5` blocks. Then the two outputs of the two `ble5` blocks go to the two outputs of `lut5inter`. Finally, there is a fully connected crossbar that connects the `lut5inter` clock input to the two `ble5` clock inputs.

Finishing out this mode, there is the last interconnect section. Note the line: `<direct name="direct1" input="fle.in[4:0]" output="lut5inter.in"/>`. It shows that out of the 6 `fle` input lines, only the first 5 lines are connected to `lut5inter`. The remaining line is unused.

### Second Mode
`<mode name="n1_lut6">` begins the definition of the second mode. In this mode, the `fle` block contains one block named `ble6` with 6 inputs and one output. Moving down the architecture, we see that it contains one LUT named `lut6` with 6 inputs and one output, and one flip-flop named `ff`. 

Moving down to this mode's `<interconnect>` block:
```
<interconnect>
    <direct name="direct1" input="fle.in" output="ble6.in"/>
    <direct name="direct2" input="ble6.out" output="fle.out[0:0]"/>
    <direct name="direct3" input="fle.clk" output="ble6.clk"/>
</interconnect>
```
we see that the input of `fle` is connected to the input of `ble6`, the output of `ble6` is connected to one output of `fle`, and the clock pins are wired together. The remaining output of `fle` is unused in this mode.

The final `<interconnect>` section takes care of the wiring inside the top-level `clb` block. There is a fully connected crossbar that takes as its input the inputs to `clb` as well as the outputs from `flb` in a feedback loop. The crossbar's outputs go to `flb`'s inputs. Then a crossbar connects the clock pins. Now recall that the first mode of `clb` uses both of `flb`'s outputs, but the second mode uses only one outputs. The lines:
```
    <direct name="clbouts1" input="fle[9:0].out[0:0]" output="clb.O[9:0]"/>
    <direct name="clbouts2" input="fle[9:0].out[1:1]" output="clb.O[19:10]"/>
```
ensure that if a logic block is completely filled by 6-LUTs, then the outputs those 6-LUTs take get evenly distributed across all four sides of the CLB instead of clumped on two sides.
